In [4]:
import numpy as np
import pandas as pd
import geopandas as gpd
import carto2gpd
from sodapy import Socrata

import holoviews as hv
import hvplot.pandas
import param as pm
import panel as pn

import altair as alt
import folium
from folium.plugins import HeatMap
from folium.plugins import MarkerCluster

ModuleNotFoundError: No module named 'carto2gpd'

In [ ]:
alt.renderers.enable('notebook');

In [4]:
# Enable Altair!
pn.extension('vega')

# Add external CSS
pn.extension(css_files=["https://codepen.io/chriddyp/pen/bWLwgP.css"])

# Load the full data set
## Divvy bike-share historic trips

In [5]:
client = Socrata("data.cityofchicago.org", 
                'GWonJMlcoqKVThtJkHvUXcBVo',
                timeout=100)
results = client.get(
    "fg6s-gzvg", 
    where="start_time >= '2018-01-01T00:00:00.000'",
    limit=4000000)

In [6]:
trips = pd.DataFrame.from_records(results)
trips.head()

trip_id               start_time                stop_time bike_id  \
0  17536702  2018-01-01T00:12:00.000  2018-01-01T00:17:00.000    3304   
1  17536703  2018-01-01T00:41:00.000  2018-01-01T00:47:00.000    5367   
2  17536704  2018-01-01T00:44:00.000  2018-01-01T01:33:00.000    4599   
3  17536706  2018-01-01T00:53:00.000  2018-01-01T00:56:00.000    3696   
4  17536705  2018-01-01T00:53:00.000  2018-01-01T01:05:00.000    2302   

  trip_duration from_station_id            from_station_name to_station_id  \
0           323              69       Damen Ave & Pierce Ave           159   
1           377             253  Winthrop Ave & Lawrence Ave           325   
2          2904              98   LaSalle St & Washington St           509   
3           183             129    Blue Island Ave & 18th St           205   
4           747             125         Rush St & Hubbard St           364   

             to_station_name   user_type gender birth_year from_latitude  \
0  Claremont Ave & Hirsch St  Subscriber   Male       1988  41.909396006   
1    Clark St & Winnemac Ave  Subscriber   Male       1984     41.968812   
2        Troy St & North Ave  Subscriber   Male       1989     41.882664   
3       Paulina St & 18th St  Subscriber   Male       1989     41.857556   
4       Larrabee St & Oak St  Subscriber   Male       1983     41.890173   

  from_longitude                                      from_location  \
0  -87.677691929  {'type': 'Point', 'coordinates': [-87.67769192...   
1     -87.657659  {'type': 'Point', 'coordinates': [-87.657659, ...   
2      -87.63253  {'type': 'Point', 'coordinates': [-87.63253, 4...   
3     -87.661535  {'type': 'Point', 'coordinates': [-87.661535, ...   
4     -87.626185  {'type': 'Point', 'coordinates': [-87.626185, ...   

    to_latitude   to_longitude  \
0     41.907781     -87.685854   
1     41.973345     -87.667682   
2  41.909769302  -87.705280487   
3     41.857901     -87.668745   
4  41.900219493  -87.642985468   

                                         to_location  
0  {'type': 'Point', 'coordinates': [-87.685854, ...  
1  {'type': 'Point', 'coordinates': [-87.667682, ...  
2  {'type': 'Point', 'coordinates': [-87.70528048...  
3  {'type': 'Point', 'coordinates': [-87.668745, ...  
4  {'type': 'Point', 'coordinates': [-87.64298546...

In [7]:
# extract the year/month/day/hour of each trip
# start time
trips['start_time'] = pd.to_datetime(trips['start_time'])
trips['start_year'] = trips['start_time'].dt.year
trips['start_month'] = trips['start_time'].dt.month
trips['start_day'] = trips['start_time'].dt.day
trips['start_hour'] = trips['start_time'].dt.hour
# stop time
trips['stop_time'] = pd.to_datetime(trips['stop_time'])
trips['stop_year'] = trips['stop_time'].dt.year
trips['stop_month'] = trips['stop_time'].dt.month
trips['stop_day'] = trips['stop_time'].dt.day
trips['stop_hour'] = trips['stop_time'].dt.hour
trips.head()

trip_id          start_time           stop_time bike_id trip_duration  \
0  17536702 2018-01-01 00:12:00 2018-01-01 00:17:00    3304           323   
1  17536703 2018-01-01 00:41:00 2018-01-01 00:47:00    5367           377   
2  17536704 2018-01-01 00:44:00 2018-01-01 01:33:00    4599          2904   
3  17536706 2018-01-01 00:53:00 2018-01-01 00:56:00    3696           183   
4  17536705 2018-01-01 00:53:00 2018-01-01 01:05:00    2302           747   

  from_station_id            from_station_name to_station_id  \
0              69       Damen Ave & Pierce Ave           159   
1             253  Winthrop Ave & Lawrence Ave           325   
2              98   LaSalle St & Washington St           509   
3             129    Blue Island Ave & 18th St           205   
4             125         Rush St & Hubbard St           364   

             to_station_name   user_type  ...   to_longitude  \
0  Claremont Ave & Hirsch St  Subscriber  ...     -87.685854   
1    Clark St & Winnemac Ave  Subscriber  ...     -87.667682   
2        Troy St & North Ave  Subscriber  ...  -87.705280487   
3       Paulina St & 18th St  Subscriber  ...     -87.668745   
4       Larrabee St & Oak St  Subscriber  ...  -87.642985468   

                                         to_location start_year start_month  \
0  {'type': 'Point', 'coordinates': [-87.685854, ...       2018           1   
1  {'type': 'Point', 'coordinates': [-87.667682, ...       2018           1   
2  {'type': 'Point', 'coordinates': [-87.70528048...       2018           1   
3  {'type': 'Point', 'coordinates': [-87.668745, ...       2018           1   
4  {'type': 'Point', 'coordinates': [-87.64298546...       2018           1   

  start_day start_hour stop_year stop_month  stop_day  stop_hour  
0         1          0      2018          1         1          0  
1         1          0      2018          1         1          0  
2         1          0      2018          1         1          1  
3         1          0      2018          1         1          0  
4         1          0      2018          1         1          1  

[5 rows x 26 columns]

In [8]:
trips = trips.loc[trips['start_year']==2018]
len(trips)

3602742

In [9]:
# store the start/end years of our data set
min_year = trips['start_year'].min()
max_year = trips['stop_year'].max()
# store the start/end months of our data set
min_month = trips['start_month'].min()
max_month = trips['stop_month'].max()
# store the start/end hours of our data set
min_hour = trips['start_hour'].min()
max_hour = trips['stop_hour'].max()

## bike-share stations

In [10]:
stations = gpd.read_file(
    'https://data.cityofchicago.org/resource/bbyy-e7gq.geojson')

# Build the app

In [11]:
# store the default min/max month
month_bounds = (min_month, max_month)
# store the default min/max hour
hour_bounds = (min_hour, max_hour)

In [11]:
# percent of user type 

In [12]:
# trips["count"] = 1
# trips.head()

In [13]:
# trips_month = trips.groupby(["start_month"])["count"].sum().reset_index()

In [14]:
# trips_month

In [15]:
# alt.Chart(trips_month).mark_bar(size=30).encode(
#     x=alt.X("start_month", axis = alt.Axis(title='Month')),
#     y=alt.Y("count",axis=alt.Axis(title="Count")),
#     tooltip=["start_month","count"]
# ).properties(
#     height=300,
#     width=500,
#     title="Trip Counts by Month"
# ).interactive()

In [16]:
# trips["trip_duration"]=trips["trip_duration"].astype(float)
# trips.head()

In [17]:
# trips_duration = trips.groupby(["start_hour"])["trip_duration"].mean().round(decimals=2).reset_index()

In [18]:
# bars = alt.Chart(trips_duration).mark_bar().encode(
#     x=alt.X("trip_duration:Q",axis=alt.Axis(title="Trip Duration")),
#     y=alt.Y("start_hour:O",axis=alt.Axis(title="Hour")),
#     tooltip=["trip_duration","start_hour"],
# ).properties(
# width=500,
# height=600,
# title="Average Trip Duration by Hour"
# )

# text = bars.mark_text(
#     align='left',
#     baseline='middle',
#     dx=3  # Nudges text to right so it doesn't appear on top of the bar
# ).encode(
#     text='trip_duration:Q'
# )

# (bars + text).properties(height=900)

In [19]:
# today = pd.to_datetime("today")
# print(today)

In [20]:
# timeFilter = hv.streams.BoundsX(boundsx=month_bounds)
# timeFilter

In [12]:
class ChicagoBikeShareApp(pm.Parameterized):
    """
    An app visualizing bike share trips in Chicago since 2018. 
    
    It includes:
    - an Altair histogram showing trip counts by month
    - an Altair stacked bar chart showing percent of user type by month
    - an Altair pie chart showing percent of male riders vs. female riders
    - an Altair bar plot showing average trip duration by hour of a day
    - a Folium map with all the stations

    
    - Data for a specific station can be selected by clicking the station 
    on the interactive map.
    
    
    There are two parameters:
    
    1. "month": the range of months to query Divvy trips for
    2. "timeFilter": the min/max of the x-axis selection (date axis)？？？
    """

    # the number of months to get data for
    month = pm.Range(default=(1,12), bounds=(1, 12))
    
    # the x-axis selection on the trip charts
#     timeFilter = hv.streams.BoundsX(boundsx=month_bounds)


    @pm.depends("month")
    def get_month(self):
        """
        Get a object holding the trip data. 
        
        Before returning, filter the trips by month range.
        """
        data=trips
        
        # trim by month range
        if self.month != (1, 12):
            data = trips.loc[(trips['start_month']>=min(self.month))&(trips['start_month']<=max(self.month))]

        return data


#     @pm.depends("month", watch=True)
#     def _reset_timeFilter(self):
#         """
#         Internal function that resets the time filter to the default limits.
        
#         This function will run anytime that the "Months" parameter changes.
#         """
#         self.timeFilter.update(boundsx=month_bounds)

    @pm.depends("month")
    def altair_hist(self): 
        """
        Return an altair histogram of the number of currently selected
        trips by month.
        """
      # get the filtered data
        data = self.get_month()
        data["count"] = 1
        trips_month = data.groupby(["start_month"])["count"].sum().reset_index()
        
        # create the chart
        chart = (
        alt.Chart(trips_month).mark_bar(size=30).encode(
          x=alt.X("start_month", axis = alt.Axis(title='Month')),
         y=alt.Y("count",axis=alt.Axis(title="Count")),
          tooltip=["start_month","count"]
         ).properties(
          height=300,
         width=300,
          title="Trip Counts by Month"
         ).interactive()
        )
        return pn.Pane(chart, width=300)  
   
    @pm.depends("month")
    def duration_bar(self):
        """
        Return an altair bar plot of average trip duration by hour of a day.
        
        """
        # Calculate and get the dataframe of the average duration by hour
        data = self.get_month()
        data["trip_duration"]=data["trip_duration"].astype(float)
        trips_duration = data.groupby(["start_hour"])["trip_duration"].mean().round(decimals=2).reset_index()
       
       # Make the bar plot
        bars = alt.Chart(trips_duration).mark_bar().encode(
            x=alt.X("trip_duration:Q",axis=alt.Axis(title="Trip Duration")),
            y=alt.Y("start_hour:O",axis=alt.Axis(title="Hour")),
            tooltip=["trip_duration","start_hour"],
        ).properties(
            width=400,
            height=300,
            title="Average Trip Duration by Hour"
        )
    
        text = bars.mark_text(
            align='left',
            baseline='middle',
            dx=3  # Nudges text to right so it doesn't appear on top of the bar
        ).encode(
            text='trip_duration:Q'
            )
    
        bars_text = (bars + text).properties(height=400)
        return pn.Pane(bars_text, width=400)
    
    @pm.depends("month")
    def usertype_stackedbar(self): 
        """
        Return an altair stacked bar chart showing percent of user type by month
        """
        
        # Groupby the trips data by month and user type.
        trips = self.get_month()
        trips_user_type = trips.groupby(
          ['start_month','user_type']
        ).size().to_frame(
            'count'
        ).unstack(level='user_type').fillna(0).stack().reset_index()
        #trips_user_type
        
        # Create the stacked bar plot
        stacked_bar = alt.Chart(trips_user_type).mark_bar().encode(
                   y=alt.Y('count:Q'),
                   x=alt.X('start_month:O'),
                   color='user_type:N',
                   tooltip=['start_month','user_type','count']
               ).properties(
                    title='Count of User Types by Month',
                    width=300,
                    height=300
                ).interactive()

        return pn.Pane(stacked_bar, width=300)  
    
    @pm.depends("month")
    def gender_horizbar(self): 
        """
        Return an altair horizontal bar showing percent of male/female riders by month
        """
        
        # Groupby the trips data by month and gender
        trips = self.get_month()
        trips_gender = trips.groupby(
            ['start_month','gender']
        ).size().reset_index(name='count')
        
        # Create the horizontal bar plot
        horizontal_bar= alt.Chart(trips_gender).mark_bar().encode(
                x=alt.X('count',stack='normalize'),
                y=alt.Y('start_month:O'),
                color='gender',
                tooltip=['start_month','gender','count']
            ).properties(
             title='Gender Ratio of Riders by Month',
                width=400,
                height=300
            ).interactive()
        return pn.Pane(horizontal_bar, width=400)  
    
    def station(self):
        """
        Return the station data.
        """
        df=stations
        return df

    @pm.depends("month")
    def folium_map(self):
        """
        Return a Folium map with a heatmap showing the currently 
        selected data.
        """
        m = folium.Map(
             location=[41.842525, -87.616987], 
              tiles='Stamen Toner',
              zoom_start=11
             )

        data = self.station()
        
        # make marker cluster
        marker_cluster = MarkerCluster().add_to(m)
        locations = data[['latitude','longitude']]
        locationlist = locations.values.tolist()
        
        for i in range(0, len(locationlist)):
            folium.Marker(locationlist[i],
                  tooltip='Station Name: '+stations['station_name'][i],
                  popup=stations.iloc[i]['total_docks']
                 ).add_to(marker_cluster)

        # IMPORTANT: add map to a folium Figure
        # return a figure with a set width/height
        figure = folium.Figure(width=400, height=800)
        m.add_to(figure)

        # return the Pane object
        return pn.Pane(figure,width=400)

#     @pm.depends("month")
#     def summary_text(self): ######## 需要figure out dataset ############
#         """
#         Get a summary of the number of shootings/homicides.
        
#         Returns an HTML <p> tag.
#         """
#         # only filter this by days
#         data = self.filter_by_days()

#         # count shootings and homicides
#         shootings = len(data)
#         homicides = (data.fatal == "Yes").sum()
#         t = f"<p>There have been {shootings:,} shootings and {homicides:,} homicides in the last {self.days} days.</p>"

#         return pn.Pane(t, width=500)

In [13]:
app = ChicagoBikeShareApp(name="")

## Layout our Panel object

We will use a combination of the `Column()` and `Row()` objects to create out layout.

In [14]:
# The title of our app
title = pn.Pane("<h3>Divvy Bike-share Trips in Chicago in 2018</h3>", width=600)

# The instructions for filtering the line chart
instructions = pn.Pane(
    """
<div font-size=28px><b>Note:</b> Data for a specific time period can be selected by clicking
and dragging a specific range on the line chart above.</div>""",
    width=500,
)

In [1]:
import holoviews as hv
import holoviews.plotting.bokeh

from bokeh.plotting import figure

fig = figure()
fig.scatter([0, 1, 2, 3, 4, 5, 6, 7, 8, 9], [0, 1, 2, 3, 2, 1, 0, -1, -2, -3])

gspec = pn.GridSpec(sizing_mode='stretch_both',max_height=900,max_width=1200)


gspec[0:1,0:4]= pn.Column(title)
gspec[0:1,4:]= app.param
gspec[1:2, 0:2] = app.altair_hist
gspec[1:2, 3] = app.duration_bar
gspec[3:5, 0:2] = app.usertype_stackedbar
gspec[3:5, 3] = app.gender_horizbar
gspec[1:10, 5:9] = app.folium_map
gspec

ModuleNotFoundError: No module named 'holoviews'

In [2]:
def plot(ticker):
    ...
    return plot_object

pn.interact(plot, ticker=['AAPL', ...])

NameError: name 'pn' is not defined

In [94]:
# Layout the panel
panel = pn.Column(
    pn.Row(pn.Column(title), app.param),
    pn.Row(app.duration_bar,app.altair_hist),
    pn.Row(app.gender_horizbar,app.usertype_stackedbar),
    pn.Row(app.folium_map,align="center"),
#     pn.Row(app.daily_shootings, align="center"),
    pn.Row(instructions, align="center"),
)

In [27]:
panel.servable()

Column
    [0] Row
        [0] Column
            [0] Markdown(str, width=600)
        [1] Column(margin=5, name='Param01382', width=300)
            [0] StaticText(value='<b></b>')
            [1] RangeSlider(end=12, name='Month', start=1, step=1, value=(1, 12))
    [1] Row
        [0] ParamMethod(method)
        [1] ParamMethod(method)
    [2] Row
        [0] ParamMethod(method)
        [1] ParamMethod(method)
    [3] Row(align='center')
        [0] ParamMethod(method)
    [4] Row(align='center')
        [0] Markdown(str, width=500)